In [1]:
!python -V

Python 3.9.12


In [1]:
# import library 
import pandas as pd 
import pickle
from sklearn.feature_extraction import DictVectorizer
from sklearn.linear_model import LinearRegression 
from sklearn.linear_model import Lasso
from sklearn.metrics import mean_squared_error

In [2]:
import mlflow

# Set the tracking URI to the same one used in your UI
mlflow.set_tracking_uri("http://127.0.0.1:5001")  

# Create or set the experiment
mlflow.set_experiment("nyc-taxi-experiment")

<Experiment: artifact_location='mlflow-artifacts:/1', creation_time=1746401851956, experiment_id='1', last_update_time=1746401851956, lifecycle_stage='active', name='nyc-taxi-experiment', tags={}>

### Put all the proccessing into a function

In [3]:
def read_dataframe(filename):
    "Write a function to read and preprocessing data"
    # Read the dataset
    df_taxi = pd.read_parquet(filename)

    # Adjust dropoff & pickup to pandas datetime 
    df_taxi['lpep_pickup_datetime'] = pd.to_datetime(df_taxi.lpep_pickup_datetime)
    df_taxi['lpep_dropoff_datetime'] = pd.to_datetime(df_taxi.lpep_dropoff_datetime)
    
    # Calculate the duration (drop_off -  pick_up)
    df_taxi['duration'] = df_taxi.lpep_dropoff_datetime - df_taxi.lpep_pickup_datetime
    
    # Adjust the duration in minutes for prediction 
    df_taxi['duration_minutes'] = df_taxi['duration'].dt.total_seconds() / 60

    # Since there are a lot of duration less than 1 minutes. We filter only duration between 1 minutes to 99% percentile
    df_taxi = df_taxi[(df_taxi['duration_minutes'] >= 1) & (df_taxi['duration_minutes'] <= 60)]

    # Feature Engineering 
    categorical_variables = ['PULocationID', 'DOLocationID']
    numerical_variables = ['trip_distance']

    # Convert it into "str"
    df_taxi[categorical_variables] = df_taxi[categorical_variables].astype(str)
    
    return df_taxi

In [4]:
df_train = read_dataframe('../00-Dataset/green_tripdata_2021-01.parquet')
df_val = read_dataframe('../00-Dataset/green_tripdata_2021-02.parquet')

In [5]:
len(df_train), len(df_val)

(73908, 61921)

### Create the training pipeline 

In [6]:
# Feature Engineering 
categorical_variables = ['PULocationID', 'DOLocationID']
numerical_variables = ['trip_distance']

# Vectorizer the training variables 
dv = DictVectorizer()

# Convert it into dictionary 
train_dicts = df_train[categorical_variables + numerical_variables].to_dict(orient = 'records')
X_train = dv.fit_transform(train_dicts)

# Create the validation set 
val_dicts = df_val[categorical_variables + numerical_variables].to_dict(orient = 'records')
X_val = dv.transform(val_dicts)

In [7]:
# Setup the Prediction_Variables 
predictor = 'duration_minutes'
y_train = df_train[predictor].values
y_val = df_val[predictor].values

In [8]:
# Train the model 
lr = LinearRegression() 
lr.fit(X_train, y_train)

# Make a prediction 
y_pred = lr.predict(X_val)

# Calculate the performance (RMSE)
mean_squared_error(y_val, y_pred, squared = False) 

10.47390313604031

### Try To Combine the input features 

In [9]:
df_train['PU_DO'] = df_train['PULocationID'] + '_' + df_train['DOLocationID']
df_val['PU_DO'] = df_val['PULocationID'] + '_' + df_val['DOLocationID']

In [10]:
# Feature Engineering 
categorical_variables = ['PU_DO']  #['PULocationID', 'DOLocationID']
numerical_variables = ['trip_distance']

# Vectorizer the training variables 
dv = DictVectorizer()

# Convert it into dictionary 
train_dicts = df_train[categorical_variables + numerical_variables].to_dict(orient = 'records')
X_train = dv.fit_transform(train_dicts)

# Create the validation set 
val_dicts = df_val[categorical_variables + numerical_variables].to_dict(orient = 'records')
X_val = dv.transform(val_dicts)

In [11]:
# Setup the Prediction_Variables 
predictor = 'duration_minutes'
y_train = df_train[predictor].values
y_val = df_val[predictor].values

In [12]:
# Train the model 
lr = LinearRegression() 
lr.fit(X_train, y_train)

# Make a prediction 
y_pred = lr.predict(X_val)

# Calculate the performance (RMSE)
mean_squared_error(y_val, y_pred, squared = False) 

7.479586896299878

In [13]:
with open('models/lin_reg.bin', 'wb') as f_out:
    pickle.dump((dv, lr), f_out)

### Try with Lasso Regression

In [74]:
# Train the model 
lr = Lasso(alpha= 0.0001) 
lr.fit(X_train, y_train)

# Make a prediction 
y_pred = lr.predict(X_val)

# Calculate the performance (RMSE)
mean_squared_error(y_val, y_pred, squared = False) 

10.47054920225702

## 2.  Using MLFlow to automated 

In [15]:
with mlflow.start_run():
    
    #set the tag name for who response
    mlflow.set_tag("developer","dario")
    
    #set the training and validation
    mlflow.log_param("train-data-path", "../00-Dataset/green_tripdata_2021-01.parquet")
    mlflow.log_param("valid-data-path", "../00-Dataset/green_tripdata_2021-02.parquet")
    
    #set the alpha
    alpha = 0.01
    mlflow.log_param("alpha", alpha)
    
    
    lr = Lasso(alpha= 0.1) 
    lr.fit(X_train, y_train)

    # Make a prediction 
    y_pred = lr.predict(X_val)

    # Calculate the performance (RMSE)
    rmse = mean_squared_error(y_val, y_pred, squared = False) 
    mlflow.log_metric("rmse", rmse)
    
    # Saving a model in artifact
    mlflow.log_artifact(local_path = "models/lin_reg.bin", artifact_path = "models_pickle") 

🏃 View run traveling-mule-376 at: http://127.0.0.1:5001/#/experiments/1/runs/220c1062753140b3b4063161911cbe11
🧪 View experiment at: http://127.0.0.1:5001/#/experiments/1


### Hyperparameter tunning with XGBoost

In [18]:
import xgboost as xgb 
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials #fmin: minimize the output
from hyperopt.pyll import scope 

In [19]:
# Create the train data 
train = xgb.DMatrix(X_train, label = y_train)
valid = xgb.DMatrix(X_val, label = y_val)

In [23]:
# define the objective function 
def objective(params):
    "Write the objective function"
    with mlflow.start_run():
        mlflow.set_tag("model", "xgboost")
        mlflow.log_params(params)
        booster = xgb.train(
            params = params,
            dtrain = train,
            num_boost_round = 1000, # n.o of iteration
            evals = [(valid, "validation")],
            early_stopping_rounds = 50
        )
        y_pred = booster.predict(valid)
        rmse = mean_squared_error(y_val, y_pred, squared = False)
        mlflow.log_metric("rmse", rmse)
    return {'loss': rmse, 'status': STATUS_OK} 

In [24]:
# define the search space 
search_space = {
    'max_depth': scope.int(hp.quniform('max_depth', 4, 100, 1)),
    'learning_rate': hp.loguniform('learning_rate', -3, 0), # exp(-3) to exp(0) --> [0.05 , 1]
    'reg_alpha': hp.loguniform('reg_alpha', -5, -1),
    'reg_lambda': hp.loguniform('reg_lambda', -6, -1),
    'min_child_weight': hp.loguniform('min_child_weight', -1, 3),
    'objective': 'reg:linear',
    'seed': 42,
}

best_result = fmin(
    fn = objective,
    space = search_space,
    algo = tpe.suggest,
    max_evals = 50,
    trials = Trials())


  0%|                                                                              | 0/50 [00:00<?, ?trial/s, best loss=?]

/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [05:18:48] WARNING: /workspace/src/objective/regression_obj.cu:227: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:11.77675                                                                                              
[1]	validation-rmse:11.37090                                                                                              
[2]	validation-rmse:10.99400                                                                                              
[3]	validation-rmse:10.64460                                                                                              
[4]	validation-rmse:10.32067                                                                                              
[5]	validation-rmse:10.02096                                                                                              
[6]	validation-rmse:9.74359                                                                                               
[7]	validation-rmse:9.48734                                                                                               
[8]	validation-r

[132]	validation-rmse:6.55328                                                                                             
[133]	validation-rmse:6.55310                                                                                             
[134]	validation-rmse:6.55286                                                                                             
[135]	validation-rmse:6.55263                                                                                             
[136]	validation-rmse:6.55240                                                                                             
[137]	validation-rmse:6.55209                                                                                             
[138]	validation-rmse:6.55144                                                                                             
[139]	validation-rmse:6.55118                                                                                             
[140]	validation

[264]	validation-rmse:6.53036                                                                                             
[265]	validation-rmse:6.53029                                                                                             
[266]	validation-rmse:6.53020                                                                                             
[267]	validation-rmse:6.53011                                                                                             
[268]	validation-rmse:6.53000                                                                                             
[269]	validation-rmse:6.52992                                                                                             
[270]	validation-rmse:6.52985                                                                                             
[271]	validation-rmse:6.52972                                                                                             
[272]	validation

...

/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [07:48:43] WARNING: /workspace/src/objective/regression_obj.cu:227: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:10.66128                                                                                              
[1]	validation-rmse:9.50168                                                                                               
[2]	validation-rmse:8.65408                                                                                               
[3]	validation-rmse:8.04127                                                                                               
[4]	validation-rmse:7.60116                                                                                               
[5]	validation-rmse:7.29409                                                                                               
[6]	validation-rmse:7.07165                                                                                               
[7]	validation-rmse:6.91336                                                                                               
[8]	validation-r

[132]	validation-rmse:6.35661                                                                                             
[133]	validation-rmse:6.35626                                                                                             
[134]	validation-rmse:6.35606                                                                                             
[135]	validation-rmse:6.35545                                                                                             
[136]	validation-rmse:6.35511                                                                                             
[137]	validation-rmse:6.35439                                                                                             
[138]	validation-rmse:6.35419                                                                                             
[139]	validation-rmse:6.35359                                                                                             
[140]	validation

[264]	validation-rmse:6.31882                                                                                             
[265]	validation-rmse:6.31878                                                                                             
[266]	validation-rmse:6.31846                                                                                             
[267]	validation-rmse:6.31740                                                                                             
[268]	validation-rmse:6.31763                                                                                             
[269]	validation-rmse:6.31701                                                                                             
[270]	validation-rmse:6.31671                                                                                             
[271]	validation-rmse:6.31670                                                                                             
[272]	validation

[396]	validation-rmse:6.30927                                                                                             
[397]	validation-rmse:6.30939                                                                                             
[398]	validation-rmse:6.30963                                                                                             
[399]	validation-rmse:6.30959                                                                                             
[400]	validation-rmse:6.30960                                                                                             
[401]	validation-rmse:6.30950                                                                                             
[402]	validation-rmse:6.30976                                                                                             
[403]	validation-rmse:6.30962                                                                                             
[404]	validation

### Second way of logging model with MLFlow

In [22]:
# Run the model with the optimal parameters 

with mlflow.start_run():
    best_params = {
        'learning_rate' : 0.09355210835495566,
        'max_depth': 48,
        'min_child_weight': 1.3066537416277637,
        'objective': 'reg:linear',
        'reg_alpha': 0.007562857391927243,
        'reg_lambda': 0.15361226750440168,
        'seed': 42
    }
    
    # log the parameters
    mlflow.log_params(best_params)
    
    # train the model
    booster = xgb.train(
            params = best_params,
            dtrain = train,
            num_boost_round = 1000, # n.o of iteration
            evals = [(valid, "validation")],
            early_stopping_rounds = 50
        )
    y_pred = booster.predict(valid)
    rmse = mean_squared_error(y_val, y_pred, squared = False)
    mlflow.log_metric("rmse", rmse)
    
    # save the preprocessing 
    with open("models/preprocessor.b", "wb") as f_out:
        pickle.dump(dv, f_out)
        
    # log the preprocessing step 
    mlflow.log_artifact("models/preprocessor.b", artifact_path = "preprocessor")
    
    # log the model
    mlflow.xgboost.log_model(booster, artifact_path = "models_mlflow")

/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [22:44:52] WARNING: /workspace/src/objective/regression_obj.cu:227: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)


[0]	validation-rmse:11.45545
[1]	validation-rmse:10.78998
[2]	validation-rmse:10.20547
[3]	validation-rmse:9.69629
[4]	validation-rmse:9.25358
[5]	validation-rmse:8.86802
[6]	validation-rmse:8.53481
[7]	validation-rmse:8.24791
[8]	validation-rmse:8.00254
[9]	validation-rmse:7.79131
[10]	validation-rmse:7.60888
[11]	validation-rmse:7.45314
[12]	validation-rmse:7.32135
[13]	validation-rmse:7.20667
[14]	validation-rmse:7.10978
[15]	validation-rmse:7.02560
[16]	validation-rmse:6.95471
[17]	validation-rmse:6.89347
[18]	validation-rmse:6.84103
[19]	validation-rmse:6.79525
[20]	validation-rmse:6.75500
[21]	validation-rmse:6.72179
[22]	validation-rmse:6.69329
[23]	validation-rmse:6.66730
[24]	validation-rmse:6.64416
[25]	validation-rmse:6.62380
[26]	validation-rmse:6.60582
[27]	validation-rmse:6.59021
[28]	validation-rmse:6.57674
[29]	validation-rmse:6.56429
[30]	validation-rmse:6.55333
[31]	validation-rmse:6.54334
[32]	validation-rmse:6.53477
[33]	validation-rmse:6.52651
[34]	validation-rmse:

[277]	validation-rmse:6.35714
[278]	validation-rmse:6.35670
[279]	validation-rmse:6.35661
[280]	validation-rmse:6.35651
[281]	validation-rmse:6.35625
[282]	validation-rmse:6.35610
[283]	validation-rmse:6.35602
[284]	validation-rmse:6.35580
[285]	validation-rmse:6.35555
[286]	validation-rmse:6.35530
[287]	validation-rmse:6.35521
[288]	validation-rmse:6.35502
[289]	validation-rmse:6.35490
[290]	validation-rmse:6.35487
[291]	validation-rmse:6.35456
[292]	validation-rmse:6.35433
[293]	validation-rmse:6.35402
[294]	validation-rmse:6.35388
[295]	validation-rmse:6.35370
[296]	validation-rmse:6.35363
[297]	validation-rmse:6.35352
[298]	validation-rmse:6.35339
[299]	validation-rmse:6.35288
[300]	validation-rmse:6.35271
[301]	validation-rmse:6.35234
[302]	validation-rmse:6.35211
[303]	validation-rmse:6.35182
[304]	validation-rmse:6.35166
[305]	validation-rmse:6.35161
[306]	validation-rmse:6.35143
[307]	validation-rmse:6.35117
[308]	validation-rmse:6.35104
[309]	validation-rmse:6.35093
[310]	vali

[551]	validation-rmse:6.31864
[552]	validation-rmse:6.31846
[553]	validation-rmse:6.31847
[554]	validation-rmse:6.31838
[555]	validation-rmse:6.31838
[556]	validation-rmse:6.31831
[557]	validation-rmse:6.31810
[558]	validation-rmse:6.31791
[559]	validation-rmse:6.31789
[560]	validation-rmse:6.31787
[561]	validation-rmse:6.31768
[562]	validation-rmse:6.31759
[563]	validation-rmse:6.31758
[564]	validation-rmse:6.31755
[565]	validation-rmse:6.31750
[566]	validation-rmse:6.31742
[567]	validation-rmse:6.31729
[568]	validation-rmse:6.31734
[569]	validation-rmse:6.31721
[570]	validation-rmse:6.31707
[571]	validation-rmse:6.31711
[572]	validation-rmse:6.31695
[573]	validation-rmse:6.31687
[574]	validation-rmse:6.31697
[575]	validation-rmse:6.31690
[576]	validation-rmse:6.31682
[577]	validation-rmse:6.31655
[578]	validation-rmse:6.31614
[579]	validation-rmse:6.31617
[580]	validation-rmse:6.31618
[581]	validation-rmse:6.31622
[582]	validation-rmse:6.31610
[583]	validation-rmse:6.31595
[584]	vali

[825]	validation-rmse:6.30407
[826]	validation-rmse:6.30410
[827]	validation-rmse:6.30406
[828]	validation-rmse:6.30408
[829]	validation-rmse:6.30398
[830]	validation-rmse:6.30400
[831]	validation-rmse:6.30408
[832]	validation-rmse:6.30403
[833]	validation-rmse:6.30402
[834]	validation-rmse:6.30397
[835]	validation-rmse:6.30401
[836]	validation-rmse:6.30395
[837]	validation-rmse:6.30392
[838]	validation-rmse:6.30397
[839]	validation-rmse:6.30399
[840]	validation-rmse:6.30399
[841]	validation-rmse:6.30407
[842]	validation-rmse:6.30406
[843]	validation-rmse:6.30386
[844]	validation-rmse:6.30383
[845]	validation-rmse:6.30373
[846]	validation-rmse:6.30382
[847]	validation-rmse:6.30396
[848]	validation-rmse:6.30400
[849]	validation-rmse:6.30395
[850]	validation-rmse:6.30394
[851]	validation-rmse:6.30394
[852]	validation-rmse:6.30395
[853]	validation-rmse:6.30389
[854]	validation-rmse:6.30386
[855]	validation-rmse:6.30391
[856]	validation-rmse:6.30399
[857]	validation-rmse:6.30398
[858]	vali

/home/codespace/anaconda3/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [22:48:47] WARNING: /workspace/src/c_api/c_api.cc:1374: Saving model in the UBJSON format as default.  You can use file extension: `json`, `ubj` or `deprecated` to choose between formats.
  warnings.warn(smsg, UserWarning)
2025/05/06 22:48:50 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: /tmp/tmp403radik/model, flavor: xgboost). Fall back to return ['xgboost==2.1.4']. Set logging level to DEBUG to see the full traceback. 
2025/05/06 22:48:50 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


🏃 View run capricious-slug-237 at: http://127.0.0.1:5001/#/experiments/1/runs/1f3bdd5050ec470d84fb45ee81d7c57e
🧪 View experiment at: http://127.0.0.1:5001/#/experiments/1


### Make a Prediction using MLFlow 

In [23]:
logged_model = 'runs:/1f3bdd5050ec470d84fb45ee81d7c57e/models_mlflow'

# Load model as a PyFuncModel.
loaded_model = mlflow.pyfunc.load_model(logged_model)

# show the result
loaded_model 

mlflow.pyfunc.loaded_model:
  artifact_path: models_mlflow
  flavor: mlflow.xgboost
  run_id: 1f3bdd5050ec470d84fb45ee81d7c57e

In [24]:
# Load the model with an xgb_model 
xgboost_model = mlflow.xgboost.load_model(logged_model)

# show the result 
xgboost_model

In [25]:
# Make a prediction 
y_pred = xgboost_model.predict(valid)

# show the top 10 prediction
y_pred[:10]

array([14.333161 ,  7.0940804, 14.959061 , 24.429314 ,  9.406549 ,
       17.154919 , 10.806144 ,  8.499913 ,  9.224104 , 18.18823  ],
      dtype=float32)